In [1]:
import pickle
import numpy as np
import pandas as pd
import math
from sklearn import metrics
from sklearn.cluster import KMeans
from sklearn.preprocessing import StandardScaler, normalize
from scipy.spatial.distance import cdist
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

In [2]:
sys.path.append(os.path.abspath(os.path.join('../scripts')))
from df_selector import *
from outliener import Outlier
from visualization import *

ModuleNotFoundError: No module named 'df_selector'

In [ ]:
pd.set_option('display.max_columns', None)
pd.set_option('display.max_colwidth', None)
pd.set_option("expand_frame_repr", False)
pd.set_option('display.float_format', '{:.2f}'.format)

In [4]:

pd.set_option('display.max_columns', 100)

In [5]:
df = pd.read_csv("../data/user_overviewed_data.csv")
df.head()


Unnamed: 0               Bearer Id                Start  Start ms                  End  End ms  Dur. (ms)               IMSI  MSISDN/Number              IMEI     Last Location Name  Avg RTT DL (ms)  Avg RTT UL (ms)  Avg Bearer TP DL (kbps)  Avg Bearer TP UL (kbps)  TCP DL Retrans. Vol (Bytes)  TCP UL Retrans. Vol (Bytes)  DL TP < 50 Kbps (%)  50 Kbps < DL TP < 250 Kbps (%)  250 Kbps < DL TP < 1 Mbps (%)  DL TP > 1 Mbps (%)  UL TP < 10 Kbps (%)  10 Kbps < UL TP < 50 Kbps (%)  50 Kbps < UL TP < 300 Kbps (%)  UL TP > 300 Kbps (%)  Activity Duration DL (ms)  Activity Duration UL (ms)   Dur. (ms).1 Handset Manufacturer                 Handset Type  Nb of sec with Vol DL < 6250B  Nb of sec with Vol UL < 1250B  Social Media DL (Bytes)  Social Media UL (Bytes)  Google DL (Bytes)  Google UL (Bytes)  Email DL (Bytes)  Email UL (Bytes)  Youtube DL (Bytes)  Youtube UL (Bytes)  Netflix DL (Bytes)  Netflix UL (Bytes)  Gaming DL (Bytes)  Gaming UL (Bytes)  Other DL (Bytes)  Other UL (Bytes)  Total UL (Bytes)  Total DL (Bytes)  Social Media Data Volume (Bytes)  Google Data Volume (Bytes)  Email Data Volume (Bytes)  Youtube Data Volume (Bytes)  Netflix Data Volume (Bytes)  Gaming Data Volume (Bytes)  Other Data Volume (Bytes)  Total Data Volume (Bytes)
0           0 13114483460844900352.00  2019-04-04 12:01:00    770.00  2019-04-25 14:35:00  662.00 1823652.00 208201448079117.00 33664962239.00 35521209507511.00  9.16456699548519E+015            42.00             5.00                    23.00                    44.00                     19520.00                      7230.00               100.00                            0.00                           0.00                0.00               100.00                           0.00                            0.00                  0.00                   37624.00                   38787.00 1823652892.00              Samsung   Samsung Galaxy A5 Sm-A520F                         213.00                         214.00               1545765.00                 24420.00         1634479.00         1271433.00        3563542.00         137762.00         15854611.00          2501332.00          8198936.00          9656251.00       278082303.00        14344150.00      171744450.00        8814393.00       36749741.00      308879636.00                        1570185.00                  2905912.00                 3701304.00                  18355943.00                  17855187.00                292426453.00               180558843.00               345629377.00
1           1 13114483482878900224.00  2019-04-09 13:04:00    235.00  2019-04-25 08:15:00  606.00 1365104.00 208201909211140.00 33681854413.00 35794009006359.00                L77566A            65.00             5.00                    16.00                    26.00                     19520.00                      7230.00               100.00                            0.00                           0.00                0.00               100.00                           0.00                            0.00                  0.00                     168.00                    3560.00 1365104371.00              Samsung  Samsung Galaxy J5 (Sm-J530)                         971.00                        1022.00               1926113.00                  7165.00         3493924.00          920172.00         629046.00         308339.00         20247395.00         19111729.00         18338413.00         17227132.00       608750074.00         1170709.00      526904238.00       15055145.00       53800391.00      653384965.00                        1933278.00                  4414096.00                  937385.00                  39359124.00                  35565545.00                609920783.00               541959383.00               707185356.00
2           2 13114483484080500736.00  2019-04-09 17:42:00      1.00  2019-04-25 11:58:00  652.00 1361762.00 208200314458056.00 33760627129.00 35281510359387.00                D42335A            65.00             5.00         

## Task 3.1



Aggregate, per customer, the following information(treat missing & outliers by replacing by the mean or the mode of the corresponding variab

Average TCP retransmission
Average RTT
Handset type
Average throughput

In [6]:
user_experience_df = df[[
    'MSISDN/Number',
    'Avg RTT DL (ms)',
    'Avg RTT UL (ms)',
    'Avg Bearer TP DL (kbps)',
    'Avg Bearer TP UL (kbps)',
    'TCP DL Retrans. Vol (Bytes)',
    'TCP UL Retrans. Vol (Bytes)',
    'Handset Type']]

In [7]:
# caluclate the totals
user_experience_df['Total Avg RTT (ms)'] = user_experience_df['Avg RTT DL (ms)'] + user_experience_df['Avg RTT UL (ms)']
user_experience_df['Total Avg Bearer TP (kbps)'] = user_experience_df['Avg Bearer TP DL (kbps)'] + user_experience_df['Avg Bearer TP UL (kbps)']
user_experience_df['Total TCP Retrans. Vol (Bytes)'] = user_experience_df['TCP DL Retrans. Vol (Bytes)'] + user_experience_df['TCP UL Retrans. Vol (Bytes)']
user_experience_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 146887 entries, 0 to 146886
Data columns (total 11 columns):
 #   Column                          Non-Null Count   Dtype  
---  ------                          --------------   -----  
 0   MSISDN/Number                   146887 non-null  float64
 1   Avg RTT DL (ms)                 146887 non-null  float64
 2   Avg RTT UL (ms)                 146887 non-null  float64
 3   Avg Bearer TP DL (kbps)         146887 non-null  float64
 4   Avg Bearer TP UL (kbps)         146887 non-null  float64
 5   TCP DL Retrans. Vol (Bytes)     146887 non-null  float64
 6   TCP UL Retrans. Vol (Bytes)     146887 non-null  float64
 7   Handset Type                    146887 non-null  object 
 8   Total Avg RTT (ms)              146887 non-null  float64
 9   Total Avg Bearer TP (kbps)      146887 non-null  float64
 10  Total TCP Retrans. Vol (Bytes)  146887 non-null  float64
dtypes: float64(10), object(1)
memory usage: 12.3+ MB


C:\Users\samrit\AppData\Local\Temp\ipykernel_7884\3507776172.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  user_experience_df['Total Avg RTT (ms)'] = user_experience_df['Avg RTT DL (ms)'] + user_experience_df['Avg RTT UL (ms)']
C:\Users\samrit\AppData\Local\Temp\ipykernel_7884\3507776172.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  user_experience_df['Total Avg Bearer TP (kbps)'] = user_experience_df['Avg Bearer TP DL (kbps)'] + user_experience_df['Avg Bearer TP UL (kbps)']
C:\Users\samrit\AppD

In [8]:
user_experience_df.head()

MSISDN/Number  Avg RTT DL (ms)  Avg RTT UL (ms)  Avg Bearer TP DL (kbps)  Avg Bearer TP UL (kbps)  TCP DL Retrans. Vol (Bytes)  TCP UL Retrans. Vol (Bytes)                 Handset Type  Total Avg RTT (ms)  Total Avg Bearer TP (kbps)  Total TCP Retrans. Vol (Bytes)
0 33664962239.00            42.00             5.00                    23.00                    44.00                     19520.00                      7230.00   Samsung Galaxy A5 Sm-A520F               47.00                       67.00                        26750.00
1 33681854413.00            65.00             5.00                    16.00                    26.00                     19520.00                      7230.00  Samsung Galaxy J5 (Sm-J530)               70.00                       42.00                        26750.00
2 33760627129.00            65.00             5.00                     6.00                     9.00                     19520.00                      7230.00     Samsung Galaxy A8 (2018)               70.00                       15.00                        26750.00
3 33750343200.00            65.00             5.00                    44.00                    44.00                     19520.00                      7230.00                      unknown               70.00                       88.00                        26750.00
4 33699795932.00            65.00             5.00                     6.00                     9.00                     19520.00                      7230.00             Samsung Sm-G390F               70.00                       15.00                        26750.00

In [9]:

# select the necessary columns
user_experience_df = user_experience_df[['MSISDN/Number', 'Handset Type', 'Total Avg RTT (ms)',
    'Total Avg Bearer TP (kbps)', 'Total TCP Retrans. Vol (Bytes)']]
user_experience_df.head()

MSISDN/Number                 Handset Type  Total Avg RTT (ms)  Total Avg Bearer TP (kbps)  Total TCP Retrans. Vol (Bytes)
0 33664962239.00   Samsung Galaxy A5 Sm-A520F               47.00                       67.00                        26750.00
1 33681854413.00  Samsung Galaxy J5 (Sm-J530)               70.00                       42.00                        26750.00
2 33760627129.00     Samsung Galaxy A8 (2018)               70.00                       15.00                        26750.00
3 33750343200.00                      unknown               70.00                       88.00                        26750.00
4 33699795932.00             Samsung Sm-G390F               70.00                       15.00                        26750.00

In [10]:
# aggregating user experience metrics per user
user_experience_df1 = user_experience_df.groupby(
    'MSISDN/Number').agg({
        'Total Avg RTT (ms)': 'sum',
        'Total Avg Bearer TP (kbps)': 'sum',
        'Total TCP Retrans. Vol (Bytes)': 'sum',
        'Handset Type': [lambda x: x.mode()[0]]})
user_experience_df1.head()

Total Avg RTT (ms) Total Avg Bearer TP (kbps) Total TCP Retrans. Vol (Bytes)                    Handset Type
                              sum                        sum                            sum                        <lambda>
MSISDN/Number                                                                                                              
33601001722.00              46.00                      76.00                     2895381.00  Huawei P20 Lite Huawei Nova 3E
33601001754.00              31.00                      99.00                     9272453.00          Apple iPhone 7 (A1778)
33601002511.00              59.00                      97.00                     4150403.00                         unknown
33601007832.00              84.00                     248.00                        2396.00         Apple iPhone 5S (A1457)
33601008617.00             119.00                   56844.00                     9738882.00         Apple iPhone Se (A1723)

In [11]:
user_experience_df = pd.DataFrame(columns=[
    "Total Avg RTT (ms)",
    "Total Avg Bearer TP (kbps)",
    "Total TCP Retrans. Vol (Bytes)",
    "Handset Type"])

user_experience_df["Total Avg RTT (ms)"] = user_experience_df1["Total Avg RTT (ms)"]['sum']
user_experience_df["Total Avg Bearer TP (kbps)"] = user_experience_df1["Total Avg Bearer TP (kbps)"]['sum']
user_experience_df["Total TCP Retrans. Vol (Bytes)"] = user_experience_df1["Total TCP Retrans. Vol (Bytes)"]['sum']
user_experience_df["Handset Type"] = user_experience_df1["Handset Type"]['<lambda>']
user_experience_df.head()

Total Avg RTT (ms)  Total Avg Bearer TP (kbps)  Total TCP Retrans. Vol (Bytes)                    Handset Type
MSISDN/Number                                                                                                                 
33601001722.00               46.00                       76.00                      2895381.00  Huawei P20 Lite Huawei Nova 3E
33601001754.00               31.00                       99.00                      9272453.00          Apple iPhone 7 (A1778)
33601002511.00               59.00                       97.00                      4150403.00                         unknown
33601007832.00               84.00                      248.00                         2396.00         Apple iPhone 5S (A1457)
33601008617.00              119.00                    56844.00                      9738882.00         Apple iPhone Se (A1723)

## Top 10 values of the experience metrics

In [12]:
# top 10 rtt values in the dataset

rtt = user_experience_df.sort_values('Total Avg RTT (ms)', ascending=False)
top_10 = rtt.head(10)['Total Avg RTT (ms)']
bottom_10 = rtt.tail(10)['Total Avg RTT (ms)']
most_10 = user_experience_df['Total Avg RTT (ms)'].value_counts().head(10)


In [13]:
plotly_multi_hist([top_10, bottom_10, most_10], 1, 3,
    "RTT values in the dataset", ['Top 10', 'Bottom 10', 'Most 10'])

In [14]:
# top 10 tp values in the dataset

tp = user_experience_df.sort_values('Total Avg Bearer TP (kbps)', ascending=False)
top_10 = tp.head(10)['Total Avg Bearer TP (kbps)']
bottom_10 = tp.tail(10)['Total Avg Bearer TP (kbps)']
most_10 = user_experience_df['Total Avg Bearer TP (kbps)'].value_counts().head(10)

In [15]:
plotly_multi_hist([top_10, bottom_10, most_10], 1, 3,
    "TP values in the dataset", ['Top 10', 'Bottom 10', 'Most 10'])

In [16]:
# top 10 tcp values in the dataset

tcp = user_experience_df.sort_values('Total TCP Retrans. Vol (Bytes)', ascending=False)
top_10 = tcp.head(10)['Total TCP Retrans. Vol (Bytes)']
bottom_10 = tcp.tail(10)['Total TCP Retrans. Vol (Bytes)']
most_10 = user_experience_df['Total TCP Retrans. Vol (Bytes)'].value_counts().head(10)

In [17]:
plotly_multi_hist([top_10, bottom_10, most_10], 1, 3,
    "TCP values in the dataset", ['Top 10', 'Bottom 10', 'Most 10'])

### Average values of experience metrics per handset type

In [18]:
handset_type_df = user_experience_df.groupby('Handset Type').mean()
handset_type_df.head()

Total Avg RTT (ms)  Total Avg Bearer TP (kbps)  Total TCP Retrans. Vol (Bytes)
Handset Type                                                                                                     
A-Link Telecom I. Cubot A5                      42.00                    23510.00                      9541170.00
A-Link Telecom I. Cubot Note Plus             1589.00                     6699.00                       616213.00
A-Link Telecom I. Cubot Note S                 890.00                     8937.00                     41411731.00
A-Link Telecom I. Cubot Nova                    44.00                    56217.00                       137170.00
A-Link Telecom I. Cubot Power                   43.00                    69468.00                         8041.00

In [19]:
# sorting per tp
tp = handset_type_df.sort_values(
    'Total Avg Bearer TP (kbps)', ascending=False)
tp.head()

Total Avg RTT (ms)  Total Avg Bearer TP (kbps)  Total TCP Retrans. Vol (Bytes)
Handset Type                                                                                                      
Spa Condor Elect. Allure M2                      90.00                   168623.00                        89016.00
Huawei Par-Lx9                                  259.00                   144115.00                      2896635.00
Huawei B715S-23C                                153.60                   141692.50                     44737973.10
Asustek Wireless-Ac1200 Lte Router              207.00                   125525.00                      8780527.00
New-Bund Technol. Thor                           81.50                   113444.50                      3949428.00

In [20]:
# sorting per tcp
tcp = handset_type_df.sort_values(
    'Total TCP Retrans. Vol (Bytes)', ascending=False)
tcp.head()

Total Avg RTT (ms)  Total Avg Bearer TP (kbps)  Total TCP Retrans. Vol (Bytes)
Handset Type                                                                                            
Simcom Wireless. Sim800H               69.00                        8.00                   4344115651.00
Lg Lg-H635                             80.33                    25339.00                    904873011.00
Sfr Star Trail 5 By Sfr               587.00                     9718.00                    432474957.00
Huawei Bln-Al10                       292.00                     5761.00                    329174592.00
Mikrotikls Sia R11E-Lte                70.00                      544.00                    321688480.00

##### K-means Clustering


In [26]:
# scale data
scaler = StandardScaler()
scaled_data = scaler.fit_transform(user_experience_df)
scaled_data

array([[-0.17015638, -0.49427243, -0.10860156],
       [-0.19190879, -0.49373249, -0.07950754],
       [-0.15130428, -0.49377944, -0.10287579],
       ...,
       [-0.16145541, -0.25273304, -0.12081633],
       [-0.17885734, -0.49333341, -0.12067974],
       [-0.14985412, -0.49528188, -0.12126092]])

In [27]:
normalized_data = normalize(scaled_data)
normalized_data

array([[-0.31870262, -0.92577146, -0.20341054],
       [-0.35827194, -0.92174253, -0.14843155],
       [-0.28732972, -0.93769659, -0.19536309],
       ...,
       [-0.49936101, -0.78167108, -0.3736695 ],
       [-0.33216904, -0.91620551, -0.22412316],
       [-0.28195947, -0.93190237, -0.22815965]])

In [28]:
kmeans = KMeans(n_clusters=3, random_state=1).fit(normalized_data)
kmeans.labels_

array([1, 1, 1, ..., 1, 1, 1])

In [29]:
user_experience_df.insert(0, 'cluster', kmeans.labels_)
user_experience_df

cluster  Total Avg RTT (ms)  Total Avg Bearer TP (kbps)  Total TCP Retrans. Vol (Bytes)
MSISDN/Number                                                                                              
33601001722.00            1               46.00                       76.00                      2895381.00
33601001754.00            1               31.00                       99.00                      9272453.00
33601002511.00            1               59.00                       97.00                      4150403.00
33601007832.00            1               84.00                      248.00                         2396.00
33601008617.00            2              119.00                    56844.00                      9738882.00
...                     ...                 ...                         ...                             ...
33789967113.00            1               53.00                       67.00                        56578.00
33789980299.00            2              109.00                   163079.00                     10617270.00
33789996170.00            1               52.00                    10365.00                       218045.00
33789997247.00            1               40.00                      116.00                       247983.00
337000037000919.00        1               60.00                       33.00                       120596.00

[105716 rows x 4 columns]

In [30]:

user_experience_df['cluster'].value_counts()

1    68953
2    28246
0     8517
Name: cluster, dtype: int64

In [31]:
fig = px.scatter(user_experience_df, x='Total TCP Retrans. Vol (Bytes)', y='Total Avg Bearer TP (kbps)',
                 color='cluster', size='Total Avg RTT (ms)')
fig.show()

In [32]:
cluster0 = user_experience_df[user_experience_df["cluster"]==0]
cluster0[["Total Avg RTT (ms)",
    "Total Avg Bearer TP (kbps)",
    "Total TCP Retrans. Vol (Bytes)"]].describe()

Total Avg RTT (ms)  Total Avg Bearer TP (kbps)  Total TCP Retrans. Vol (Bytes)
count             8517.00                     8517.00                         8517.00
mean               952.69                    10725.30                    190011175.28
std               2251.06                    18375.58                    675569583.55
min                  8.00                        0.00                          216.00
25%                298.00                      219.00                       205339.00
50%                445.00                     3966.00                      1744550.00
75%                924.00                    15910.00                     12164593.00
max              96924.00                   379713.00                   8354209105.00

In [33]:
cluster1 = user_experience_df[user_experience_df["cluster"]==1]
cluster1[["Total Avg RTT (ms)",
    "Total Avg Bearer TP (kbps)",
    "Total TCP Retrans. Vol (Bytes)"]].describe()

Total Avg RTT (ms)  Total Avg Bearer TP (kbps)  Total TCP Retrans. Vol (Bytes)
count            68953.00                    68953.00                        68953.00
mean                65.82                     2017.62                      5660428.17
std                 48.61                     4632.40                     18696690.40
min                  0.00                        0.00                           51.00
25%                 33.00                       87.00                        47682.00
50%                 49.00                      112.00                       376782.00
75%                 79.00                      449.00                      2798756.00
max                301.00                    21802.00                    288468626.00

In [34]:
cluster2 = user_experience_df[user_experience_df["cluster"]==2]
cluster2[["Total Avg RTT (ms)",
    "Total Avg Bearer TP (kbps)",
    "Total TCP Retrans. Vol (Bytes)"]].describe()

Total Avg RTT (ms)  Total Avg Bearer TP (kbps)  Total TCP Retrans. Vol (Bytes)
count            28246.00                    28246.00                        28246.00
mean               163.39                    70926.77                     28816282.01
std                187.36                    56860.98                    179534839.35
min                 19.00                    21218.00                           97.00
25%                 67.00                    35771.50                       428203.25
50%                103.00                    53179.50                      2428174.00
75%                180.00                    83874.50                     10308920.75
max               5847.00                   902222.00                   5879989037.00

### Saving Data

In [35]:
# save the dataframe
user_experience_df.to_csv('../data/user_experience_data.csv')

In [36]:
# save the clustering model
with open("../models/user_experience.pkl", "wb") as f:
    pickle.dump(kmeans, f)